In [1]:
import random
import math
import time

def gameBoard():
    tictacBoard = {
        1: ' ', 2: ' ', 3: ' ',
        4: ' ', 5: ' ', 6: ' ',
        7: ' ', 8: ' ', 9: ' '
    }
    defaultPlayerMark = 'X'
    minMaxMark = 'O'
    return tictacBoard, defaultPlayerMark, minMaxMark

def printGame(gamegrid):
    print("\n")
    separator = "\n" + "-"*9 + "\n"
    formatted_grid = separator.join(
        " | ".join(gamegrid[i+j] for j in range(3)) for i in range(1, 10, 3)
    )
    print(formatted_grid)
    print()


def isLegal(gamegrid, move):
    if move in gamegrid:
        return gamegrid[move] == ' '
    else:
        return False 


def isDraw(gamegrid):
    return ' ' not in gamegrid.values() and not isSuccess(gamegrid)

def isSuccess(gamegrid):
    wincombi = [
        (1, 2, 3), (4, 5, 6), (7, 8, 9),
        (1, 4, 7), (2, 5, 8), (3, 6, 9),
        (1, 5, 9), (7, 5, 3)
    ]

    for combo in wincombi:
        if gamegrid[combo[0]] == gamegrid[combo[1]] == gamegrid[combo[2]] != ' ':
            return True

    return False

def isSuccessMark(gamegrid, mark):
    winplace = [
        (1, 2, 3), (4, 5, 6), (7, 8, 9),
        (1, 4, 7), (2, 5, 8), (3, 6, 9),
        (1, 5, 9), (7, 5, 3)
    ]

    for pos in winplace:
        if all(gamegrid[i] == mark for i in pos):
            return True
    return False

def new_turn(gamegrid):
    position = random.randint(1, 9)
    while not isLegal(gamegrid, position):
        position = random.randint(1, 9)
    return position

def defaultPlayer(gamegrid, playermark):
    for availablemoves in gamegrid.keys():
        if gamegrid[availablemoves] == ' ':
            gamegrid[availablemoves] = playermark
            
            if isSuccess(gamegrid):
                gamegrid[availablemoves] = ' '
                position = availablemoves
                break
                
            elif isDraw(gamegrid):
                gamegrid[availablemoves] = ' '
                position = availablemoves
                break
                
            else:
                gamegrid[availablemoves] = ' '
                position = new_turn(gamegrid)

        if 'position' in locals():  
            gamegrid[position] = playermark
            return gamegrid

    return gamegrid  

def minMax(gamegrid, playermarker, player2mark, depthm):
    best_scr = -math.inf
    best_pos = new_turn(gamegrid)

    for availablemoves in gamegrid.keys():
        if gamegrid[availablemoves] == ' ':
            gamegrid[availablemoves] = playermarker
            curr_scr = minMax_eval(gamegrid, False, -math.inf, math.inf, playermarker, player2mark, isSuccessMark, isDraw, 0, depthm) 
            gamegrid[availablemoves] = ' '

            if curr_scr > best_scr:
                best_scr = curr_scr
                best_pos = availablemoves

    if best_pos is not None:
        gamegrid[best_pos] = playermarker
    return gamegrid



def minMax_eval(gamegrid, ismovem, alpha, beta, minMaxMark, defaultPlayerMark, isSuccessMark, isDraw,depth, depthm):
    if isSuccessMark(gamegrid, minMaxMark):
        return 1
    elif isSuccessMark(gamegrid, defaultPlayerMark):
        return -1
    elif isDraw(gamegrid):
        return 0

    if ismovem:
        best_scr = -math.inf
        for availablemoves in gamegrid.keys():
            if gamegrid[availablemoves] == ' ':
                gamegrid[availablemoves] = minMaxMark
                curr_scr = minMax_eval(gamegrid, False, alpha, beta, minMaxMark, defaultPlayerMark, isSuccessMark, isDraw , depth+1,depthm)
                gamegrid[availablemoves] = ' '

                best_scr = max(best_scr, curr_scr)
                alpha = max(alpha, best_scr)

                if alpha >= beta:
                    break

        return best_scr

    else:
        best_scr = math.inf
        for availablemoves in gamegrid.keys():
            if gamegrid[availablemoves] == ' ':
                gamegrid[availablemoves] = defaultPlayerMark
                curr_scr = minMax_eval(gamegrid, True, alpha, beta, minMaxMark, defaultPlayerMark, isSuccessMark, isDraw,depth+1,depthm)
                gamegrid[availablemoves] = ' '

                best_scr = min(best_scr, curr_scr)
                beta = min(beta, best_scr)

                if alpha >= beta:
                    break

        return best_scr
    

def gamestate(gamegrid, curr_mark, player2mark):
    pts = 0
    wingrids = [
        (1, 2, 3), (4, 5, 6), (7, 8, 9),  
        (1, 4, 7), (2, 5, 8), (3, 6, 9),  
        (1, 5, 9), (3, 5, 7)               
    ]

    for a, b, c in wingrids:
        ln = [gamegrid[a], gamegrid[b], gamegrid[c]]
        if ln.count(curr_mark) == 2 and ln.count(' ') == 1:
            pts += 10 
        if ln.count(player2mark) == 2 and ln.count(' ') == 1:
            pts -= 10 

    return pts


def minMax_scr(gamegrid, ismovemx, curr_mark, player2mark, depth, depthm):
    if depth >= depthm: 
        return gamestate(gamegrid, curr_mark, player2mark)  

    if isSuccessMark(gamegrid, curr_mark):
        return 1 if ismovemx else -1
    elif isSuccessMark(gamegrid, player2mark):
        return -1 if ismovemx else 1
    elif isDraw(gamegrid):
        return 0

    if ismovemx:
        best_scr = -math.inf
        for availablemoves in gamegrid.keys():
            if gamegrid[availablemoves] == ' ':
                gamegrid[availablemoves] = curr_mark
                curr_scr = minMax_scr(gamegrid, not ismovemx, player2mark, curr_mark, depth + 1, depthm)
                gamegrid[availablemoves] = ' '
                best_scr = max(best_scr, curr_scr)
        return best_scr
    else:
        best_scr = math.inf
        for availablemoves in gamegrid.keys():
            if gamegrid[availablemoves] == ' ':
                gamegrid[availablemoves] = player2mark
                curr_scr = minMax_scr(gamegrid, not ismovemx, player2mark, curr_mark, depth + 1, depthm)
                gamegrid[availablemoves] = ' '
                best_scr = min(best_scr, curr_scr)
        return best_scr

def move_mm(gamegrid, minMaxMark, player2mark, depthm):
    best_scr = -math.inf
    best_pos = None
    for availablemoves in gamegrid.keys():
        if gamegrid[availablemoves] == ' ':
            gamegrid[availablemoves] = minMaxMark
            curr_scr = minMax_scr(gamegrid, True, minMaxMark, player2mark, 0, depthm)
            gamegrid[availablemoves] = ' '

            if curr_scr > best_scr:
                best_scr = curr_scr
                best_pos = availablemoves

    if best_pos is not None:
        gamegrid[best_pos] = minMaxMark
    return gamegrid



In [2]:
def play_game(depthm=15, defaultfirst=True, abprune=False):
    gamegrid, defaultPlayerMark, minMaxMark = gameBoard()

    while True:
        if defaultfirst:
            print("Default Players Move:")
            gamegrid = defaultPlayer(gamegrid, defaultPlayerMark)
            printGame(gamegrid)
            if isSuccessMark(gamegrid, defaultPlayerMark):
                return 'Default Player Wins'
            if isDraw(gamegrid):
                return 'Draw'
        else:
            print("MinMax Player's Move:")
            if abprune:
                gamegrid = minMax(gamegrid, minMaxMark, defaultPlayerMark, depthm)
            else:
                gamegrid = move_mm(gamegrid, minMaxMark, defaultPlayerMark, depthm)
            printGame(gamegrid)
            if isSuccessMark(gamegrid, minMaxMark):
                return 'MinMaxWon'
            if isDraw(gamegrid):
                return 'Draw'

        defaultfirst = not defaultfirst


In [3]:

def runGames(firstplay, gamealgo):
    time_taken = 0
    win_default = win_minmax = drawgame = 0

    for _ in range(games):
        startTime = time.time()
        try:
            winner = gamealgo()
            if winner == 'MinMaxWon':
                win_minmax += 1
            elif winner == 'Default Player Wins':
                win_default += 1
            else:
                drawgame += 1
        except Exception as e:
            print(f"Error occurred: {e}")
        finally:
            time_taken += time.time() - startTime

    print(f"Simulation: {firstplay}")
    print(f"Total Time: {time_taken} seconds")
    print(f"Default Player Wins: {win_default}, MinMax Wins: {win_minmax}, Draws: {drawgame}")
    print()



In [4]:

games = 50

runGames("Default Player starts first without pruning", lambda: play_game(depthm=15, defaultfirst=True, abprune=False))


Default Players Move:


  |   | X
---------
  |   |  
---------
  |   |  

MinMax Player's Move:


O |   | X
---------
  |   |  
---------
  |   |  

Default Players Move:


O |   | X
---------
  |   |  
---------
X |   |  

MinMax Player's Move:


O | O | X
---------
  |   |  
---------
X |   |  

Default Players Move:


O | O | X
---------
  |   | X
---------
X |   |  

MinMax Player's Move:


O | O | X
---------
O |   | X
---------
X |   |  

Default Players Move:


O | O | X
---------
O |   | X
---------
X |   |  

MinMax Player's Move:


O | O | X
---------
O | O | X
---------
X |   |  

Default Players Move:


O | O | X
---------
O | O | X
---------
X | X |  

MinMax Player's Move:


O | O | X
---------
O | O | X
---------
X | X | O

Default Players Move:


  |   |  
---------
  |   | X
---------
  |   |  

MinMax Player's Move:


O |   |  
---------
  |   | X
---------
  |   |  

Default Players Move:


O |   |  
---------
  |   | X
---------
  | X |  

MinMax Player's Move:


O

In [5]:
games = 2000
runGames("MinMax starts first without pruning", lambda: play_game(depthm=15, defaultfirst=False, abprune=False))


MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
X |   |  
---------
  |   |  

MinMax Player's Move:


O | O |  
---------
X |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O | O |  
---------
X | X |  
---------
  |   |  

MinMax Player's Move:


O | O | O
---------
X | X |  
---------
  |   |  

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
  |   |  
---------
X |   |  

MinMax Player's Move:


O | O |  
---------
  |   |  
---------
X |   |  

Semi-Intelligent Agent's Move:


O | O |  
---------
  |   |  
---------
X | X |  

MinMax Player's Move:


O | O | O
---------
  |   |  
---------
X | X |  

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   | X
---------
  |   |  
---------
  |   |  

MinMax Player's Move:


O | O | X
---------
  |   |  
-

In [6]:
games = 2000
runGames("Random player starts first without pruning", lambda: play_game(depthm=15, defaultfirst=random.choice([True, False]), abprune=False))


Semi-Intelligent Agent's Move:


  |   |  
---------
  |   |  
---------
X |   |  

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
X |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
  |   |  
---------
X | X |  

MinMax Player's Move:


O | O |  
---------
  |   |  
---------
X | X |  

Semi-Intelligent Agent's Move:


O | O | X
---------
  |   |  
---------
X | X |  

MinMax Player's Move:


O | O | X
---------
O |   |  
---------
X | X |  

Semi-Intelligent Agent's Move:


O | O | X
---------
O |   |  
---------
X | X |  

MinMax Player's Move:


O | O | X
---------
O | O |  
---------
X | X |  

Semi-Intelligent Agent's Move:


O | O | X
---------
O | O | X
---------
X | X |  

MinMax Player's Move:


O | O | X
---------
O | O | X
---------
X | X | O

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
  |   |  
---------
X |   |  

MinMax Player's Move:


O | O |  
---------
  



X | O |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


X | O |  
---------
  |   | X
---------
  |   |  

MinMax Player's Move:


X | O | O
---------
  |   | X
---------
  |   |  

Semi-Intelligent Agent's Move:


X | O | O
---------
  | X | X
---------
  |   |  

MinMax Player's Move:


X | O | O
---------
O | X | X
---------
  |   |  

Semi-Intelligent Agent's Move:


X | O | O
---------
O | X | X
---------
  | X |  

MinMax Player's Move:


X | O | O
---------
O | X | X
---------
O | X |  

Semi-Intelligent Agent's Move:


X | O | O
---------
O | X | X
---------
O | X |  

MinMax Player's Move:


X | O | O
---------
O | X | X
---------
O | X | O

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
  |   | X
---------
  |   |  

MinMax Player's Move:


O | O |  
---------
  |   | X
---------
  |   |  

Semi-Intelligent Agent's Move:


O | O |  
---------
X |   | X
---------
  | 

In [7]:
games = 2000
runGames("Default Player starts first with pruning", lambda: play_game(depthm=6, defaultfirst=True, abprune=True))


Semi-Intelligent Agent's Move:


  |   |  
---------
  |   | X
---------
  |   |  

MinMax Player's Move:


  |   | O
---------
  |   | X
---------
  |   |  

Semi-Intelligent Agent's Move:


  |   | O
---------
X |   | X
---------
  |   |  

MinMax Player's Move:


  |   | O
---------
X | O | X
---------
  |   |  

Semi-Intelligent Agent's Move:


  | X | O
---------
X | O | X
---------
  |   |  

MinMax Player's Move:


O | X | O
---------
X | O | X
---------
  |   |  

Semi-Intelligent Agent's Move:


O | X | O
---------
X | O | X
---------
X |   |  

MinMax Player's Move:


O | X | O
---------
X | O | X
---------
X |   | O

Semi-Intelligent Agent's Move:


  |   |  
---------
X |   |  
---------
  |   |  

MinMax Player's Move:


O |   |  
---------
X |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
X |   |  
---------
  |   | X

MinMax Player's Move:


O |   | O
---------
X |   |  
---------
  |   | X

Semi-Intelligent Agent's Move:


O |   | O
---

In [5]:
games = 50
runGames("MinMax starts first with pruning", lambda: play_game(depthm=6, defaultfirst=False, abprune=True))


MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Default Players Move:


O |   |  
---------
  |   |  
---------
  | X |  

MinMax Player's Move:


O |   | O
---------
  |   |  
---------
  | X |  

Default Players Move:


O |   | O
---------
  |   |  
---------
  | X | X

MinMax Player's Move:


O | O | O
---------
  |   |  
---------
  | X | X

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Default Players Move:


O | X |  
---------
  |   |  
---------
  |   |  

MinMax Player's Move:


O | X |  
---------
O |   |  
---------
  |   |  

Default Players Move:


O | X | X
---------
O |   |  
---------
  |   |  

MinMax Player's Move:


O | X | X
---------
O | O |  
---------
  |   |  

Default Players Move:


O | X | X
---------
O | O |  
---------
X |   |  

MinMax Player's Move:


O | X | X
---------
O | O | O
---------
X |   |  

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Default Players Move:


O

In [6]:
games = 2000
runGames("Random player starts first with pruning", lambda: play_game(depthm=6, defaultfirst=random.choice([True, False]), abprune=True))

Semi-Intelligent Agent's Move:


  |   |  
---------
  |   |  
---------
  |   | X

MinMax Player's Move:


  |   |  
---------
  | O |  
---------
  |   | X

Semi-Intelligent Agent's Move:


  |   | X
---------
  | O |  
---------
  |   | X

MinMax Player's Move:


  |   | X
---------
  | O | O
---------
  |   | X

Semi-Intelligent Agent's Move:


  |   | X
---------
X | O | O
---------
  |   | X

MinMax Player's Move:


O |   | X
---------
X | O | O
---------
  |   | X

Semi-Intelligent Agent's Move:


O |   | X
---------
X | O | O
---------
  | X | X

MinMax Player's Move:


O |   | X
---------
X | O | O
---------
O | X | X

Semi-Intelligent Agent's Move:


O |   | X
---------
X | O | O
---------
O | X | X

MinMax Player's Move:


O | O | X
---------
X | O | O
---------
O | X | X

MinMax Player's Move:


O |   |  
---------
  |   |  
---------
  |   |  

Semi-Intelligent Agent's Move:


O |   |  
---------
  | X |  
---------
  |   |  

MinMax Player's Move:


O | O |  
---------
  